# Dependencies

- pandas
- koalas
- Pyspark (default)

In [0]:
import pandas as pd
import numpy as np
import databricks.koalas as ks

# DATASETS ARE PLACED IN SQL TABLES

- see code below

# Toronto AirBnB GeoJSON DataSet

- [neighbourhoods.geojson](http://data.insideairbnb.com/canada/on/toronto/2021-02-08/visualisations/neighbourhoods.geojson)
- not used in DataBricks but will be used in Power BI Desktop

# Toronto AirBnB Neighbourhoods DataSet

- [neighbourhoods.csv](http://data.insideairbnb.com/canada/on/toronto/2021-02-08/visualisations/neighbourhoods.csv)
- kind of redundant as listings.csv.gz already contains this information but I included it anyway just in case

In [0]:
URL = r"http://data.insideairbnb.com/canada/on/toronto/2021-02-08/visualisations/neighbourhoods.csv"
df_neighbour = ks.from_pandas(pd.read_csv(URL))
df_neighbour.head()

Out[24]:

neighbourhood_group 
 neighbourhood 
 
 
 
 
 0 
 NaN 
 Agincourt North 
 
 
 1 
 NaN 
 Agincourt South-Malvern West 
 
 
 2 
 NaN 
 Alderwood 
 
 
 3 
 NaN 
 Annex 
 
 
 4 
 NaN 
 Banbury-Don Mills

In [0]:
df_neighbour.print_schema()

/databricks/python/lib/python3.8/site-packages/databricks/koalas/frame.py:5938: FutureWarning: DataFrame.print_schema is deprecated as of DataFrame.spark.print_schema. Please use the API instead.
 warnings.warn(
root
-- neighbourhood_group: double (nullable = true)
-- neighbourhood: string (nullable = false)

In [0]:
spark.sql("drop table if exists AirBnb_NEIGHBOUR")
spark.sql("drop view if exists AirBnb_NEIGHBOUR_TEMP")
df_neighbour.to_spark().createOrReplaceTempView("AirBnb_NEIGHBOUR_TEMP")
spark.sql("create table AirBnb_NEIGHBOUR as select * from AirBnb_NEIGHBOUR_TEMP")
del df_neighbour

In [0]:
%sql

SELECT * FROM AirBnb_NEIGHBOUR LIMIT 5;

neighbourhood_group neighbourhood null Agincourt North null Agincourt South-Malvern West null Alderwood null Annex null Banbury-Don Mills

## Listings.csv.gz

- contains the AirBnb listing and relevant data
  - geospatial
  - price
  - minimum nights
  - tonnes of free text
  - etc.


## Reviews.csv.gz

- contains:
  - the date in which a review was done
  - listing id
  - name of the reviewer
  - review left (free text)

# 2021 Toronto AirBnb Dataset

- Feb
- [Feb. 08 2021 listings.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-02-08/data/listings.csv.gz)
- [Feb. 08 2021 reviews.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-02-08/data/reviews.csv.gz)
- Jan
- [Jan. 11 2021 listings.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-01-11/data/listings.csv.gz)
- [Jan. 11 2021 reviews.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-01-11/data/reviews.csv.gz)
- [Jan. 02 2021 listings.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-01-02/data/listings.csv.gz)
- [Jan. 02 2021 reviews.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2021-01-02/data/reviews.csv.gz)

In [0]:
# Combine all the listings in one dataset
URL_List = [
  "http://data.insideairbnb.com/canada/on/toronto/2021-02-08/data/listings.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2021-01-11/data/listings.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2021-01-02/data/listings.csv.gz"
]

# read all the csv into a dictionary
df_dict = dict()
for index, URL in enumerate(URL_List):
  df_dict[index] = ks.from_pandas(pd.read_csv(URL, compression="gzip"))
  
# ensure columns have the same format
for index, URL in enumerate(URL_List[1:]):
  df_dict[index].columns = df_dict[0].columns
  
df_2021_listings = df_dict[0].append(df_dict[1]).append(df_dict[2])
df_2021_listings.head()

Out[27]:

id 
 listing_url 
 scrape_id 
 last_scraped 
 name 
 description 
 neighborhood_overview 
 picture_url 
 host_id 
 host_url 
 host_name 
 host_since 
 host_location 
 host_about 
 host_response_time 
 host_response_rate 
 host_acceptance_rate 
 host_is_superhost 
 host_thumbnail_url 
 host_picture_url 
 host_neighbourhood 
 host_listings_count 
 host_total_listings_count 
 host_verifications 
 host_has_profile_pic 
 host_identity_verified 
 neighbourhood 
 neighbourhood_cleansed 
 neighbourhood_group_cleansed 
 latitude 
 longitude 
 property_type 
 room_type 
 accommodates 
 bathrooms 
 bathrooms_text 
 bedrooms 
 beds 
 amenities 
 price 
 minimum_nights 
 maximum_nights 
 minimum_minimum_nights 
 maximum_minimum_nights 
 minimum_maximum_nights 
 maximum_maximum_nights 
 minimum_nights_avg_ntm 
 maximum_nights_avg_ntm 
 calendar_updated 
 has_availability 
 availability_30 
 availability_60 
 availability_90 
 availability_365 
 calendar_last_scraped 
 number_of_reviews 
 number_of_reviews_ltm 
 number_of_reviews_l30d 
 first_review 
 last_review 
 review_scores_rating 
 review_scores_accuracy 
 review_scores_cleanliness 
 review_scores_checkin 
 review_scores_communication 
 review_scores_location 
 review_scores_value 
 license 
 instant_bookable 
 calculated_host_listings_count 
 calculated_host_listings_count_entire_homes 
 calculated_host_listings_count_private_rooms 
 calculated_host_listings_count_shared_rooms 
 reviews_per_month 
 
 
 
 
 0 
 1419 
 https://www.airbnb.com/rooms/1419 
 20210208155315 
 2021-02-09 
 Beautiful home in amazing area! 
 This large, family home is located in one of T... 
 The apartment is located in the Ossington stri... 
 https://a0.muscache.com/pictures/76206750/d643... 
 1565 
 https://www.airbnb.com/users/show/1565 
 Alexandra 
 2008-08-08 
 Vancouver, British Columbia, Canada 
 I live in Vancouver, Canada with my husband an... 
 None 
 None 
 None 
 f 
 https://a0.muscache.com/im/pictures/user/7aeea... 
 https://a0.muscache.com/im/pictures/user/7aeea... 
 Commercial Drive 
 1.0 
 1.0 
 ['email', 'phone', 'reviews', 'jumio', 'govern... 
 t 
 t 
 Toronto, Ontario, Canada 
 Little Portugal 
 NaN 
 43.64617 
 -79.42451 
 Entire house 
 Entire home/apt 
 10 
 NaN 
 3 baths 
 5.0 
 7.0 
 ["TV", "Washer", "Heating", "First aid kit", "... 
 $469.00 
 28 
 730 
 28 
 28 
 730 
 730 
 28.0 
 730.0 
 NaN 
 t 
 0 
 0 
 0 
 0 
 2021-02-09 
 7 
 0 
 0 
 2015-07-19 
 2017-12-04 
 100.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 None 
 f 
 1 
 1 
 0 
 0 
 0.10 
 
 
 1 
 8077 
 https://www.airbnb.com/rooms/8077 
 20210208155315 
 2021-02-09 
 Downtown Harbourfront Private Room 
 Guest room in a luxury condo with access to al... 
 None 
 https://a0.muscache.com/pictures/11780344/141c... 
 22795 
 https://www.airbnb.com/users/show/22795 
 Kathie & Larry 
 2009-06-22 
 Toronto, Ontario, Canada 
 My husband and I have been airbnb host for alm... 
 None 
 None 
 None 
 f 
 https://a0.muscache.com/im/pictures/user/9a077... 
 https://a0.muscache.com/im/pictures/user/9a077... 
 Harbourfront 
 2.0 
 2.0 
 ['email', 'phone', 'facebook', 'reviews'] 
 t 
 f 
 None 
 Waterfront Communities-The Island 
 NaN 
 43.64105 
 -79.37628 
 Private room in apartment 
 Private room 
 2 
 NaN 
 1.5 baths 
 1.0 
 1.0 
 ["Cable TV", "TV", "Heating", "Elevator", "Fre... 
 $96.00 
 180 
 365 
 180 
 180 
 365 
 365 
 180.0 
 365.0 
 NaN 
 t 
 30 
 60 
 90 
 365 
 2021-02-09 
 169 
 0 
 0 
 2009-08-20 
 2013-08-27 
 97.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 None 
 t 
 2 
 1 
 1 
 0 
 1.21 
 
 
 2 
 23691 
 https://www.airbnb.com/rooms/23691 
 20210208155315 
 2021-02-11 
 Queen Bedroom close to downtown 
 <b>The space</b><br />Nestled in the middle of... 
 None 
 https://a0.muscache.com/pictures/615528/d09ab3... 
 93825 
 https://www.airbnb.com/users/show/93825 
 Yohan & Sarah 
 2010-03-15 
 Toronto, Ontario, Canada 
 Welcome to our dwelling place! My wife and I l... 
 None 
 None 
 None 
 f 
 https://a0.muscache.com/im/use

In [0]:
df_2021_listings.print_schema()

/databricks/python/lib/python3.8/site-packages/databricks/koalas/frame.py:5938: FutureWarning: DataFrame.print_schema is deprecated as of DataFrame.spark.print_schema. Please use the API instead.
 warnings.warn(
root
-- id: long (nullable = false)
-- listing_url: string (nullable = false)
-- scrape_id: long (nullable = false)
-- last_scraped: string (nullable = false)
-- name: string (nullable = true)
-- description: string (nullable = true)
-- neighborhood_overview: string (nullable = true)
-- picture_url: string (nullable = false)
-- host_id: long (nullable = false)
-- host_url: string (nullable = false)
-- host_name: string (nullable = true)
-- host_since: string (nullable = true)
-- host_location: string (nullable = true)
-- host_about: string (nullable = true)
-- host_response_time: string (nullable = true)
-- host_response_rate: string (nullable = true)
-- host_acceptance_rate: string (nullable = true)
-- host_is_superhost: string (nullable = true)
-- host_thumbnail_url: string (nullable = true)
-- host_picture_url: string (nullable = true)
-- host_neighbourhood: string (nullable = true)
-- host_listings_count: double (nullable = true)
-- host_total_listings_count: double (nullable = true)
-- host_verifications: string (nullable = false)
-- host_has_profile_pic: string (nullable = true)
-- host_identity_verified: string (nullable = true)
-- neighbourhood: string (nullable = true)
-- neighbourhood_cleansed: string (nullable = false)
-- neighbourhood_group_cleansed: double (nullable = true)
-- latitude: double (nullable = false)
-- longitude: double (nullable = false)
-- property_type: string (nullable = false)
-- room_type: string (nullable = false)
-- accommodates: long (nullable = false)
-- bathrooms: double (nullable = true)
-- bathrooms_text: string (nullable = true)
-- bedrooms: double (nullable = true)
-- beds: double (nullable = true)
-- amenities: string (nullable = false)
-- price: string (nullable = false)
-- minimum_nights: long (nullable = false)
-- maximum_nights: long (nullable = false)
-- minimum_minimum_nights: long (nullable = false)
-- maximum_minimum_nights: long (nullable = false)
-- minimum_maximum_nights: long (nullable = false)
-- maximum_maximum_nights: long (nullable = false)
-- minimum_nights_avg_ntm: double (nullable = false)
-- maximum_nights_avg_ntm: double (nullable = false)
-- calendar_updated: double (nullable = true)
-- has_availability: string (nullable = false)
-- availability_30: long (nullable = false)
-- availability_60: long (nullable = false)
-- availability_90: long (nullable = false)
-- availability_365: long (nullable = false)
-- calendar_last_scraped: string (nullable = false)
-- number_of_reviews: long (nullable = false)
-- number_of_reviews_ltm: long (nullable = false)
-- number_of_reviews_l30d: long (nullable = false)
-- first_review: string (nullable = true)
-- last_review: string (nullable = true)
-- review_scores_rating: double (nullable = true)
-- review_scores_accuracy: double (nullable = true)
-- review_scores_cleanliness: double (nullable = true)
-- review_scores_checkin: double (nullable = true)
-- review_scores_communication: double (nullable = true)
-- review_scores_location: double (nullable = true)
-- review_scores_value: double (nullable = true)
-- license: string (nullable = true)
-- instant_bookable: string (nullable = false)
-- calculated_host_listings_count: long (nullable = false)
-- calculated_host_listings_count_entire_homes: long (nullable = false)
-- calculated_host_listings_count_private_rooms: long (nullable = false)
-- calculated_host_listings_count_shared_rooms: long (nullable = false)
-- reviews_per_month: double (nullable = true)

In [0]:
spark.sql("drop table if exists AirBnb_2021_LISTINGS")
spark.sql("drop view if exists AirBnb_2021_LISTINGS_TEMP")
df_2021_listings.to_spark().createOrReplaceTempView("AirBnb_2021_LISTINGS_TEMP")
spark.sql("create table AirBnb_2021_LISTINGS as select * from AirBnb_2021_LISTINGS_TEMP")
del df_dict, df_2021_listings

In [0]:
%sql

SELECT * FROM AirBnb_2021_LISTINGS LIMIT 5;

id listing_url scrape_id last_scraped name description neighborhood_overview picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed latitude longitude property_type room_type accommodates bathrooms bathrooms_text bedrooms beds amenities price minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm number_of_reviews_l30d first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value license instant_bookable calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 1419 https://www.airbnb.com/rooms/1419 20210208155315 2021-02-09 Beautiful home in amazing area! This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. The space Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. The apartment is located in the Ossington strip between Dundas and Queen, a fabulous, family-friendly and incredibly fun area with amazing restaurants, cafes and shops. It is considered one of Toronto's best neighbourhoods (see (URL HIDDEN) https://a0.muscache.com/pictures/76206750/d64310e4_original.jpg 1565 https://www.airbnb.com/users/show/1565 Alexandra 2008-08-08 Vancouver, British Columbia, Canada I live in Vancouver, Canada with my husband and two sons. We love to travel! null null null f https://a0.muscache.com/im/pictures/user/7aeea16d-829a-4d68-8dff-6c9c0ce1d3bf.jpg?aki_policy=profile_small https://a0.muscache.com/im/pictures/user/7aeea16d-829a-4d68-8dff-6c9c0ce1d3bf.jpg?aki_policy=profile_x_medium Commercial Drive 1.0 1.0 ['email', 'phone', 'reviews', 'jumio', 'government_id'] t t Toronto, Ontario, Canada Little Portugal null 43.64617 -79.42451 Entire house Entire home/apt 10 null 3 baths 5.0 7.0 ["TV", "Washer", "Heating", "First aid kit", "Kitchen", "Long term stays allowed", "Dryer", "Air conditioning", "Fire extinguisher", "Indoor fireplace", "Smoke alarm", "Essentials", "Wifi", "Shampoo"] $469.00 28 730 28 28 730 730 28.0 730.0 null t 0 0 0 0 2021-02-09 7 0 0 2015-07-19 2017-12-04 100.0 10.0 10.0 10.0 10.0 10.0 10.0 null f 1 1 0 0 0.1 8077 https://www.airbnb.com/rooms/8077 20210208155315 2021-02-09 Downtown Harbourfront Private Room Guest room in a luxury condo with access to all amenities, a view of downtown Toronto and a private entrance. The space My husband and I are both artists. I give painting and felting workshops and Larry is a filmmaker. We live in a split-level waterfront condo in downt

In [0]:
# Combine all the reviews in one dataset
URL_List = [
  "http://data.insideairbnb.com/canada/on/toronto/2021-02-08/data/reviews.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2021-01-11/data/reviews.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2021-01-02/data/reviews.csv.gz"
]

# read all the csv into a dictionary
df_dict = dict()
for index, URL in enumerate(URL_List):
  df_dict[index] = ks.from_pandas(pd.read_csv(URL, compression="gzip"))
  
# ensure columns have the same format
for index, URL in enumerate(URL_List[1:]):
  df_dict[index].columns = df_dict[0].columns
  
df_2021_reviews = df_dict[0].append(df_dict[1]).append(df_dict[2])
df_2021_reviews.head()

Out[30]:

listing_id 
 id 
 date 
 reviewer_id 
 reviewer_name 
 comments 
 
 
 
 
 0 
 1419 
 38924112 
 2015-07-19 
 11308465 
 Marcela 
 Having the opportunity of arriving to Alexandr... 
 
 
 1 
 1419 
 44791978 
 2015-08-29 
 9580285 
 Marco 
 We have no enough words to describe how beauty... 
 
 
 2 
 1419 
 45957133 
 2015-09-07 
 38394721 
 Andrea 
 The listing was exceptional and an even better... 
 
 
 3 
 1419 
 67295154 
 2016-03-28 
 3515044 
 Shaun 
 Alexandra's home was amazing and in such a nea... 
 
 
 4 
 1419 
 177702208 
 2017-08-03 
 13987100 
 Kate 
 Beautiful home. Very comfortable and clean. Pe...

In [0]:
df_2021_reviews.print_schema()

/databricks/python/lib/python3.8/site-packages/databricks/koalas/frame.py:5938: FutureWarning: DataFrame.print_schema is deprecated as of DataFrame.spark.print_schema. Please use the API instead.
 warnings.warn(
root
-- listing_id: long (nullable = false)
-- id: long (nullable = false)
-- date: string (nullable = false)
-- reviewer_id: long (nullable = false)
-- reviewer_name: string (nullable = false)
-- comments: string (nullable = true)

In [0]:
spark.sql("drop table if exists AirBnb_2021_REVIEWS")
spark.sql("drop view if exists AirBnb_2021_REVIEWS_TEMP")
df_2021_reviews.to_spark().createOrReplaceTempView("AirBnb_2021_REVIEWS_TEMP")
spark.sql("create table AirBnb_2021_REVIEWS as select * from AirBnb_2021_REVIEWS_TEMP")
del df_dict, df_2021_reviews

In [0]:
%sql

SELECT * FROM AirBnb_2021_REVIEWS LIMIT 5;

listing_id id date reviewer_id reviewer_name comments 1419 38924112 2015-07-19 11308465 Marcela Having the opportunity of arriving to Alexandra's house, describes that moments when you feel blessed by God. The house is super beautiful, mega equippied, easy to mantain tidy and clean. And she and her family had been a super host. The neigbourhood is calm and pretty, and near two beautiful streets: Dundas on one side and Queen in the other. We felt very very comfortable and happy at their home. We have no more than THANKS to Alex and her family. Best stay we had ever. 
 1419 44791978 2015-08-29 9580285 Marco We have no enough words to describe how beautyful and cozy is Alexandra's house. Every detail is tasteful and functional. our kids have been stunned when they've seen the toys room and tree house.
We loved this home as it if were our. Thank you!! 1419 45957133 2015-09-07 38394721 Andrea The listing was exceptional and an even better experience of it in person. The house is beautiful and so accommodating for our group. Anything we could have needed was available and the experience of working with Alexandra was wonderful! The neighborhood is very easy to get around and there's a ton of great restaurants, coffee shops and stores within walking distance. It is definitely one of the nicest houses I've ever had the chance to stay in! Anyone would be lucky to get the same experience in this great home, in a great city! 1419 67295154 2016-03-28 3515044 Shaun Alexandra's home was amazing and in such a neat neighbourhood! Everything was as described and in great condition. The rooms are great sizes and the third floor room with the sleeping nook and the outdoor deck was fantastic!

Anyone looking for a quiet neighbourhood that's only a short streetcar ride or car trip away from the downtown core stay here!

Thanks Alexandra! 1419 177702208 2017-08-03 13987100 Kate Beautiful home. Very comfortable and clean. Perfect for a family or families traveling together. Close to amazing restaurents. 
Alexandra gave us à very complete list of all sorts of useful information including nice running routes for the sporti ones. 

Highly highly recommend this house.

Kate

# 2020 Toronto AirBnb Dataset

- Feb
- [Feb. 14 2020 listings.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2020-02-14/data/listings.csv.gz)
- [Feb. 14 2020 reviews.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2020-02-14/data/reviews.csv.gz)
- Jan
- [Jan. 07 2020 listings.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2020-01-07/data/listings.csv.gz)
- [Jan. 07 2020 reviews.csv.gz](http://data.insideairbnb.com/canada/on/toronto/2020-01-07/data/reviews.csv.gz)

In [0]:
# Combine all the listings in one dataset
URL_List = [
  "http://data.insideairbnb.com/canada/on/toronto/2020-02-14/data/listings.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2020-01-07/data/listings.csv.gz"
]

# read all the csv into a dictionary
df_dict = dict()
for index, URL in enumerate(URL_List):
  df_dict[index] = ks.from_pandas(pd.read_csv(URL, compression="gzip"))
  
# ensure columns have the same format
for index, URL in enumerate(URL_List[1:]):
  df_dict[index].columns = df_dict[0].columns
  
df_2020_listings = df_dict[0].append(df_dict[1])
df_2020_listings.head()

/databricks/python/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3146: DtypeWarning: Columns (61,62) have mixed types.Specify dtype option on import or set low_memory=False.
 has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
Out[33]:

id 
 listing_url 
 scrape_id 
 last_scraped 
 name 
 summary 
 space 
 description 
 experiences_offered 
 neighborhood_overview 
 notes 
 transit 
 access 
 interaction 
 house_rules 
 thumbnail_url 
 medium_url 
 picture_url 
 xl_picture_url 
 host_id 
 host_url 
 host_name 
 host_since 
 host_location 
 host_about 
 host_response_time 
 host_response_rate 
 host_acceptance_rate 
 host_is_superhost 
 host_thumbnail_url 
 host_picture_url 
 host_neighbourhood 
 host_listings_count 
 host_total_listings_count 
 host_verifications 
 host_has_profile_pic 
 host_identity_verified 
 street 
 neighbourhood 
 neighbourhood_cleansed 
 neighbourhood_group_cleansed 
 city 
 state 
 zipcode 
 market 
 smart_location 
 country_code 
 country 
 latitude 
 longitude 
 is_location_exact 
 property_type 
 room_type 
 accommodates 
 bathrooms 
 bedrooms 
 beds 
 bed_type 
 amenities 
 square_feet 
 price 
 weekly_price 
 monthly_price 
 security_deposit 
 cleaning_fee 
 guests_included 
 extra_people 
 minimum_nights 
 maximum_nights 
 minimum_minimum_nights 
 maximum_minimum_nights 
 minimum_maximum_nights 
 maximum_maximum_nights 
 minimum_nights_avg_ntm 
 maximum_nights_avg_ntm 
 calendar_updated 
 has_availability 
 availability_30 
 availability_60 
 availability_90 
 availability_365 
 calendar_last_scraped 
 number_of_reviews 
 number_of_reviews_ltm 
 first_review 
 last_review 
 review_scores_rating 
 review_scores_accuracy 
 review_scores_cleanliness 
 review_scores_checkin 
 review_scores_communication 
 review_scores_location 
 review_scores_value 
 requires_license 
 license 
 jurisdiction_names 
 instant_bookable 
 is_business_travel_ready 
 cancellation_policy 
 require_guest_profile_picture 
 require_guest_phone_verification 
 calculated_host_listings_count 
 calculated_host_listings_count_entire_homes 
 calculated_host_listings_count_private_rooms 
 calculated_host_listings_count_shared_rooms 
 reviews_per_month 
 
 
 
 
 0 
 1419 
 https://www.airbnb.com/rooms/1419 
 20200214161839 
 2020-02-14 
 Beautiful home in amazing area! 
 This large, family home is located in one of T... 
 Visit Toronto with this fabulous furnished hom... 
 This large, family home is located in one of T... 
 none 
 The apartment is located in the Ossington stri... 
 To learn a little more about our home, see: (U... 
 All forms of public transportation are easily ... 
 The whole house and garden are available. 
 We will be out of town, but fully accessible b... 
 This is our much-loved family home. We expect ... 
 NaN 
 NaN 
 https://a0.muscache.com/im/pictures/76206750/d... 
 NaN 
 1565 
 https://www.airbnb.com/users/show/1565 
 Alexandra 
 2008-08-08 
 Toronto, Ontario, Canada 
 I live in Toronto, Canada with my husband and ... 
 None 
 None 
 None 
 f 
 https://a0.muscache.com/im/users/1565/profile_... 
 https://a0.muscache.com/im/users/1565/profile_... 
 Commercial Drive 
 1.0 
 1.0 
 ['email', 'phone', 'reviews', 'jumio', 'govern... 
 t 
 t 
 Toronto, ON, Canada 
 Little Portugal 
 Little Portugal 
 NaN 
 Toronto 
 ON 
 M6J 
 Toronto 
 Toronto, Canada 
 CA 
 Canada 
 43.64617 
 -79.42451 
 f 
 House 
 Entire home/apt 
 10 
 3.0 
 5.0 
 7.0 
 Real Bed 
 {TV,Internet,Wifi,"Air conditioning",Kitchen,"... 
 1400.0 
 $469.00 
 $2,000.00 
 None 
 $1,000.00 
 $150.00 
 1 
 $0.00 
 4 
 730 
 4 
 4 
 730 
 730 
 4.0 
 730.0 
 25 months ago 
 t 
 0 
 0 
 0 
 0 
 2020-02-14 
 7 
 0 
 2015-07-19 
 2017-12-04 
 100.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 10.0 
 f 
 NaN 
 None 
 f 
 f 
 strict_14_with_grace_period 
 f 
 f 
 1 
 1 
 0 
 0 
 0.13 
 
 
 1 
 8077 
 https://www.airbnb.com/rooms/8077 
 20200214161839 
 2020-02-15 
 Downtown Harbourfront Private Room 
 Guest room in a luxury condo with access to al... 
 My husband and I are both artists. I give pain... 
 Guest room in a luxury condo with access to al... 
 none 
 None 
 None 
 None 
 None 
 None 
 No smoking please. 
 NaN 
 NaN 
 https://a0.muscache.com/im/pictures/11780344/1... 
 NaN 
 22795 
 https://

In [0]:
df_2020_listings.print_schema()

/databricks/python/lib/python3.8/site-packages/databricks/koalas/frame.py:5938: FutureWarning: DataFrame.print_schema is deprecated as of DataFrame.spark.print_schema. Please use the API instead.
 warnings.warn(
root
-- id: long (nullable = false)
-- listing_url: string (nullable = false)
-- scrape_id: long (nullable = false)
-- last_scraped: string (nullable = false)
-- name: string (nullable = true)
-- summary: string (nullable = true)
-- space: string (nullable = true)
-- description: string (nullable = true)
-- experiences_offered: string (nullable = false)
-- neighborhood_overview: string (nullable = true)
-- notes: string (nullable = true)
-- transit: string (nullable = true)
-- access: string (nullable = true)
-- interaction: string (nullable = true)
-- house_rules: string (nullable = true)
-- thumbnail_url: double (nullable = true)
-- medium_url: double (nullable = true)
-- picture_url: string (nullable = false)
-- xl_picture_url: double (nullable = true)
-- host_id: long (nullable = false)
-- host_url: string (nullable = false)
-- host_name: string (nullable = true)
-- host_since: string (nullable = true)
-- host_location: string (nullable = true)
-- host_about: string (nullable = true)
-- host_response_time: string (nullable = true)
-- host_response_rate: string (nullable = true)
-- host_acceptance_rate: string (nullable = true)
-- host_is_superhost: string (nullable = true)
-- host_thumbnail_url: string (nullable = true)
-- host_picture_url: string (nullable = true)
-- host_neighbourhood: string (nullable = true)
-- host_listings_count: double (nullable = true)
-- host_total_listings_count: double (nullable = true)
-- host_verifications: string (nullable = false)
-- host_has_profile_pic: string (nullable = true)
-- host_identity_verified: string (nullable = true)
-- street: string (nullable = false)
-- neighbourhood: string (nullable = true)
-- neighbourhood_cleansed: string (nullable = false)
-- neighbourhood_group_cleansed: double (nullable = true)
-- city: string (nullable = true)
-- state: string (nullable = true)
-- zipcode: string (nullable = true)
-- market: string (nullable = true)
-- smart_location: string (nullable = false)
-- country_code: string (nullable = false)
-- country: string (nullable = false)
-- latitude: double (nullable = false)
-- longitude: double (nullable = false)
-- is_location_exact: string (nullable = false)
-- property_type: string (nullable = false)
-- room_type: string (nullable = false)
-- accommodates: long (nullable = false)
-- bathrooms: double (nullable = true)
-- bedrooms: double (nullable = true)
-- beds: double (nullable = true)
-- bed_type: string (nullable = false)
-- amenities: string (nullable = false)
-- square_feet: double (nullable = true)
-- price: string (nullable = false)
-- weekly_price: string (nullable = true)
-- monthly_price: string (nullable = true)
-- security_deposit: string (nullable = true)
-- cleaning_fee: string (nullable = true)
-- guests_included: long (nullable = false)
-- extra_people: string (nullable = false)
-- minimum_nights: long (nullable = false)
-- maximum_nights: long (nullable = false)
-- minimum_minimum_nights: long (nullable = false)
-- maximum_minimum_nights: long (nullable = false)
-- minimum_maximum_nights: long (nullable = false)
-- maximum_maximum_nights: long (nullable = false)
-- minimum_nights_avg_ntm: double (nullable = false)
-- maximum_nights_avg_ntm: double (nullable = false)
-- calendar_updated: string (nullable = false)
-- has_availability: string (nullable = false)
-- availability_30: long (nullable = false)
-- availability_60: long (nullable = false)
-- availability_90: long (nullable = false)
-- availability_365: long (nullable = false)
-- calendar_last_scraped: string (nullable = false)
-- number_of_reviews: long (nullable = false)
-- number_of_reviews_ltm: long (nullable = false)
-- first_review: string (nullable = true)
-- last_review: string (nullable = true)
-- review_scores_rating: double (nullable = true)
-- review

In [0]:
spark.sql("drop table if exists AirBnb_2020_LISTINGS")
spark.sql("drop view if exists AirBnb_2020_LISTINGS_TEMP")
df_2020_listings.to_spark().createOrReplaceTempView("AirBnb_2020_LISTINGS_TEMP")
spark.sql("create table AirBnb_2020_LISTINGS as select * from AirBnb_2020_LISTINGS_TEMP")
del df_dict, df_2020_listings

In [0]:
%sql

SELECT * FROM AirBnb_2020_LISTINGS LIMIT 5;

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 1419 https://www.airbnb.com/rooms/1419 20200214161839 2020-02-14 Beautiful home in amazing area! This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. The whole house and garden are available. We will be out of to none The apartment is located in the Ossington strip between Dundas and Queen, a fabulous, family-friendly and incredibly fun area with amazing restaurants, cafes and shops. It is considered one of Toronto's best neighbourhoods (s

In [0]:
# Combine all the reviews in one dataset
URL_List = [
  "http://data.insideairbnb.com/canada/on/toronto/2020-02-14/data/reviews.csv.gz"
  , "http://data.insideairbnb.com/canada/on/toronto/2020-01-07/data/reviews.csv.gz"
]

# read all the csv into a dictionary
df_dict = dict()
for index, URL in enumerate(URL_List):
  df_dict[index] = ks.from_pandas(pd.read_csv(URL, compression="gzip"))
  
# ensure columns have the same format
for index, URL in enumerate(URL_List[1:]):
  df_dict[index].columns = df_dict[0].columns
  
df_2020_reviews = df_dict[0].append(df_dict[1])
df_2020_reviews.head()

Out[36]:

listing_id 
 id 
 date 
 reviewer_id 
 reviewer_name 
 comments 
 
 
 
 
 0 
 1419 
 38924112 
 2015-07-19 
 11308465 
 Marcela 
 Having the opportunity of arriving to Alexandr... 
 
 
 1 
 1419 
 44791978 
 2015-08-29 
 9580285 
 Marco 
 We have no enough words to describe how beauty... 
 
 
 2 
 1419 
 45957133 
 2015-09-07 
 38394721 
 Andrea 
 The listing was exceptional and an even better... 
 
 
 3 
 1419 
 67295154 
 2016-03-28 
 3515044 
 Shaun 
 Alexandra's home was amazing and in such a nea... 
 
 
 4 
 1419 
 177702208 
 2017-08-03 
 13987100 
 Kate 
 Beautiful home. Very comfortable and clean. Pe...

In [0]:
df_2020_reviews.print_schema()

/databricks/python/lib/python3.8/site-packages/databricks/koalas/frame.py:5938: FutureWarning: DataFrame.print_schema is deprecated as of DataFrame.spark.print_schema. Please use the API instead.
 warnings.warn(
root
-- listing_id: long (nullable = false)
-- id: long (nullable = false)
-- date: string (nullable = false)
-- reviewer_id: long (nullable = false)
-- reviewer_name: string (nullable = false)
-- comments: string (nullable = true)

In [0]:
spark.sql("drop table if exists AirBnb_2020_REVIEWS")
spark.sql("drop view if exists AirBnb_2020_REVIEWS_TEMP")
df_2020_reviews.to_spark().createOrReplaceTempView("AirBnb_2020_REVIEWS_TEMP")
spark.sql("create table AirBnb_2020_REVIEWS as select * from AirBnb_2020_REVIEWS_TEMP")
del df_dict, df_2020_reviews

In [0]:
%sql

SELECT * FROM AirBnb_2020_REVIEWS LIMIT 5;

listing_id id date reviewer_id reviewer_name comments 1419 38924112 2015-07-19 11308465 Marcela Having the opportunity of arriving to Alexandra's house, describes that moments when you feel blessed by God. The house is super beautiful, mega equippied, easy to mantain tidy and clean. And she and her family had been a super host. The neigbourhood is calm and pretty, and near two beautiful streets: Dundas on one side and Queen in the other. We felt very very comfortable and happy at their home. We have no more than THANKS to Alex and her family. Best stay we had ever. 
 1419 44791978 2015-08-29 9580285 Marco We have no enough words to describe how beautyful and cozy is Alexandra's house. Every detail is tasteful and functional. our kids have been stunned when they've seen the toys room and tree house.
We loved this home as it if were our. Thank you!! 1419 45957133 2015-09-07 38394721 Andrea The listing was exceptional and an even better experience of it in person. The house is beautiful and so accommodating for our group. Anything we could have needed was available and the experience of working with Alexandra was wonderful! The neighborhood is very easy to get around and there's a ton of great restaurants, coffee shops and stores within walking distance. It is definitely one of the nicest houses I've ever had the chance to stay in! Anyone would be lucky to get the same experience in this great home, in a great city! 1419 67295154 2016-03-28 3515044 Shaun Alexandra's home was amazing and in such a neat neighbourhood! Everything was as described and in great condition. The rooms are great sizes and the third floor room with the sleeping nook and the outdoor deck was fantastic!

Anyone looking for a quiet neighbourhood that's only a short streetcar ride or car trip away from the downtown core stay here!

Thanks Alexandra! 1419 177702208 2017-08-03 13987100 Kate Beautiful home. Very comfortable and clean. Perfect for a family or families traveling together. Close to amazing restaurents. 
Alexandra gave us à very complete list of all sorts of useful information including nice running routes for the sporti ones. 

Highly highly recommend this house.

Kate

In [0]:
# Drop all Views keep tables only

spark.sql("drop view if exists AirBnb_NEIGHBOUR_TEMP")
spark.sql("drop view if exists AirBnb_2021_LISTINGS_TEMP")
spark.sql("drop view if exists AirBnb_2021_REVIEWS_TEMP")
spark.sql("drop view if exists AirBnb_2020_LISTINGS_TEMP")
spark.sql("drop view if exists AirBnb_2020_REVIEWS_TEMP")

Out[39]: DataFrame[]

# UTILIZE THE TABLES FOR ANALYSIS

- use pyspark and / or koalas from here on

In [0]:
%sql

SHOW TABLES;

database tableName isTemporary default airbnb_2020_listings false default airbnb_2020_reviews false default airbnb_2021_listings false default airbnb_2021_reviews false default airbnb_neighbour false default cleaned_taxes false default departuredelayswindow false default diamonds false default fireservicecalls false

## Read Data from Table into PySpark DataFrame

In [0]:
df = sqlContext.sql("SELECT * FROM airbnb_2020_listings")
display(df), type(df)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 1419 https://www.airbnb.com/rooms/1419 20200214161839 2020-02-14 Beautiful home in amazing area! This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. The whole house and garden are available. We will be out of to none The apartment is located in the Ossington strip between Dundas and Queen, a fabulous, family-friendly and incredibly fun area with amazing restaurants, cafes and shops. It is considered one of Toronto's best neighbourhoods (s

Out[40]: (None, pyspark.sql.dataframe.DataFrame)

## Read Data from SQL Table into Koalas DataFrame

In [0]:
df = ks.DataFrame(sqlContext.sql("SELECT * FROM airbnb_2020_listings"))
display(df), type(df)

id listing_url scrape_id last_scraped name summary space description experiences_offered neighborhood_overview notes transit access interaction house_rules thumbnail_url medium_url picture_url xl_picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified street neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed city state zipcode market smart_location country_code country latitude longitude is_location_exact property_type room_type accommodates bathrooms bedrooms beds bed_type amenities square_feet price weekly_price monthly_price security_deposit cleaning_fee guests_included extra_people minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value requires_license license jurisdiction_names instant_bookable is_business_travel_ready cancellation_policy require_guest_profile_picture require_guest_phone_verification calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month 1419 https://www.airbnb.com/rooms/1419 20200214161839 2020-02-14 Beautiful home in amazing area! This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. This large, family home is located in one of Toronto's most vibrant downtown neighbourhoods. The five-bedroom, three-bath house is newly renovated and complete with all the amenities you'll need for a fabulous time in the city. Visit Toronto with this fabulous furnished home as your base! This lovely home is surrounded by gardens in the back and front. Inside, you'll find a large open space with a modern kitchen and bright living and dining room. There are two floors up - a master bedroom with a king-size bed and two kids rooms, each with a single bed. The attic is a private space with a king-sized bed, fold-out single couch and a private deck. The basement is fully-finished with a private room and bath, as well as a playroom with another single couch that doubles as a sleeping space. The house will comfortably sleep 10. For kids of all ages: we have toys, a very cool tree fort, and many great parks and playgrounds nearby. The whole house and garden are available. We will be out of to none The apartment is located in the Ossington strip between Dundas and Queen, a fabulous, family-friendly and incredibly fun area with amazing restaurants, cafes and shops. It is considered one of Toronto's best neighbourhoods (s

Out[41]: (None, databricks.koalas.frame.DataFrame)

## Read Data from SQL Table into Pandas DataFrame

- dont really know why you would like to do this but here it is

In [0]:
df = sqlContext.sql("SELECT * FROM airbnb_2020_listings").toPandas()
df, type(df)

Out[42]: ( id ... reviews_per_month
 0 1419 ... 0.13
 1 8077 ... 1.34
 2 12604 ... NaN
 3 23691 ... 1.86
 4 26654 ... 0.35
 ... ... ... ...
 46917 42279466 ... NaN
 46918 42280836 ... NaN
 46919 42281530 ... NaN
 46920 42282147 ... NaN
 46921 42289607 ... NaN
 
 [46922 rows x 106 columns],
 pandas.core.frame.DataFrame)

In [0]:
# delete the df
del df

# YOUR CODE GOES IN THE CELLS BELOW